In [1]:
!py --version

Python 3.10.11


In [2]:
import torch
print(torch.__version__)
print("CUDA available:", torch.cuda.is_available())
print("GPU:", torch.cuda.get_device_name(0) if torch.cuda.is_available() else "CPU")

2.6.0+cu118
CUDA available: True
GPU: NVIDIA GeForce RTX 2050


## Import Libraries

In [1]:
import pandas as pd
import matplotlib.pyplot as plt

from neuralforecast import NeuralForecast
from neuralforecast.models import TimeXer, LSTM, TimeLLM
from neuralforecast.losses.pytorch import MSE, MAE, RMSE, QuantileLoss 

## Load Data

In [2]:
data_raw = pd.read_csv("Kolkata-daily.csv",  parse_dates=['time', 'sunrise (iso8601)', 'sunset (iso8601)'])
data_raw.head()

time  temperature_2m_mean (°C)  temperature_2m_max (°C)  \
0 1975-01-01                      19.3                     25.9   
1 1975-01-02                      20.3                     27.0   
2 1975-01-03                      20.0                     25.1   
3 1975-01-04                      19.6                     25.6   
4 1975-01-05                      18.0                     24.0   

   temperature_2m_min (°C)  rain_sum (mm)  sunshine_duration (s)  \
0                     13.3            0.0               35364.91   
1                     12.6            0.0               35346.28   
2                     15.9            0.0               29732.62   
3                     14.8            0.0               35341.67   
4                     12.8            0.0               35385.59   

   precipitation_hours (h)  dew_point_2m_mean (°C)  \
0                        0                     9.6   
1                        0                    13.0   
2                        0                    12.7   
3                        0                    11.1   
4                        0                     8.0   

   winddirection_10m_dominant (°)  wind_speed_10m_max (km/h)  \
0                              64                        9.4   
1                             150                        8.4   
2                              11                       10.1   
3                             354                       14.4   
4                             339                       12.8   

    sunrise (iso8601)    sunset (iso8601)  
0 1975-01-01 06:16:00 1975-01-01 17:02:00  
1 1975-01-02 06:16:00 1975-01-02 17:03:00  
2 1975-01-03 06:17:00 1975-01-03 17:03:00  
3 1975-01-04 06:17:00 1975-01-04 17:04:00  
4 1975-01-05 06:17:00 1975-01-05 17:05:00

## Format Data to fit Neuralforecast

In [3]:
data = data_raw.copy()
#data.rename(columns={'time': 'ds'}, inplace=True)
#data.rename(columns={'rain_sum (mm)': 'y'}, inplace=True)
data['sunrise (iso8601)'] = data['sunrise (iso8601)'].dt.time
data['sunset (iso8601)'] = data['sunset (iso8601)'].dt.time
data['sunrise'] = data['sunrise (iso8601)'].apply(lambda t: t.hour * 3600 + t.minute * 60 + t.second)
data['sunset'] = data['sunset (iso8601)'].apply(lambda t: t.hour * 3600 + t.minute * 60 + t.second)
data.drop(columns=['sunrise (iso8601)', 'sunset (iso8601)'], inplace=True)
data['unique_id'] = 1.0
data

time  temperature_2m_mean (°C)  temperature_2m_max (°C)  \
0     1975-01-01                      19.3                     25.9   
1     1975-01-02                      20.3                     27.0   
2     1975-01-03                      20.0                     25.1   
3     1975-01-04                      19.6                     25.6   
4     1975-01-05                      18.0                     24.0   
...          ...                       ...                      ...   
18356 2025-04-04                      30.2                     34.2   
18357 2025-04-05                      31.8                     38.5   
18358 2025-04-06                      31.0                     37.8   
18359 2025-04-07                      30.2                     36.8   
18360 2025-04-08                      29.2                     35.5   

       temperature_2m_min (°C)  rain_sum (mm)  sunshine_duration (s)  \
0                         13.3            0.0               35364.91   
1                         12.6            0.0               35346.28   
2                         15.9            0.0               29732.62   
3                         14.8            0.0               35341.67   
4                         12.8            0.0               35385.59   
...                        ...            ...                    ...   
18356                     26.1            0.0               13585.84   
18357                     26.2            0.0               41434.78   
18358                     26.3            1.0               39600.00   
18359                     25.6            0.3               37035.58   
18360                     26.0            3.3               39425.64   

       precipitation_hours (h)  dew_point_2m_mean (°C)  \
0                            0                     9.6   
1                            0                    13.0   
2                            0                    12.7   
3                            0                    11.1   
4                            0                     8.0   
...                        ...                     ...   
18356                        0                    21.8   
18357                        0                    18.9   
18358                        2                    22.3   
18359                        1                    21.7   
18360                        6                    22.5   

       winddirection_10m_dominant (°)  wind_speed_10m_max (km/h)  sunrise  \
0                                  64                        9.4    22560   
1                                 150                        8.4    22560   
2                                  11                       10.1    22620   
3                                 354                       14.4    22620   
4                                 339                       12.8    22620   
...                               ...                        ...      ...   
18356                             226                       10.6    19560   
18357                             227                       14.3    19500   
18358                             182                       17.9    19440   
18359                             161                       15.3    19380   
18360                             160                       12.5    19320   

       sunset  unique_id  
0       61320        1.0  
1       61380        1.0  
2       61380        1.0  
3       61440        1.0  
4       61500        1.0  
...       ...        ...  
18356   64320        1.0  
18357   64380        1.0  
18358   64380        1.0  
18359   64380        1.0  
18360   64440        1.0  

[18361 rows x 13 columns]

In [4]:
test_size = data.index[data['time'] == '2020-12-31']
data_train = data.loc[data.index <= test_size[0]]
data_test = data.loc[data.index > test_size[0]]

In [5]:
print(f"Training from {data_train['time'].min().date()} to {data_train['time'].max().date()}, size = {len(data_train)}")
print(f"Testing from {data_test['time'].min().date()} to {data_test['time'].max().date()}, size = {len(data_test)}")

Training from 1975-01-01 to 2020-12-31, size = 16802
Testing from 2021-01-01 to 2025-04-08, size = 1559


In [6]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18361 entries, 0 to 18360
Data columns (total 13 columns):
 #   Column                          Non-Null Count  Dtype         
---  ------                          --------------  -----         
 0   time                            18361 non-null  datetime64[ns]
 1   temperature_2m_mean (°C)        18361 non-null  float64       
 2   temperature_2m_max (°C)         18361 non-null  float64       
 3   temperature_2m_min (°C)         18361 non-null  float64       
 4   rain_sum (mm)                   18361 non-null  float64       
 5   sunshine_duration (s)           18361 non-null  float64       
 6   precipitation_hours (h)         18361 non-null  int64         
 7   dew_point_2m_mean (°C)          18361 non-null  float64       
 8   winddirection_10m_dominant (°)  18361 non-null  int64         
 9   wind_speed_10m_max (km/h)       18361 non-null  float64       
 10  sunrise                         18361 non-null  int64         
 11  su

## Training LSTM Model

In [7]:
horizon = 7
model_lstm_max = [LSTM(input_size = 30,            # Length of input sequence
               h=horizon,                    # Forecast horizon
               max_steps = 1200,                # Number of steps to train
               scaler_type='standard',       # Type of scaler to normalize data
               loss=MSE(),            # Loss function to use for training
               learning_rate=0.0001,
               early_stop_patience_steps=10,          # Number of epochs with no improvement after which training will be stopped
               batch_size=128,                  # Size of each batch
               encoder_n_layers=10,             # Number of layers in the encoder LSTM
               encoder_hidden_size=128,       # Defines the size of the hidden state of the LSTM
               decoder_layers=2,             # Number of layers in the decoder LSTM
               decoder_hidden_size=128,)]     # Defines the number of hidden units of each layer of the MLP 
nf_lstm_max = NeuralForecast(models=model_lstm_max, freq='D')
nf_lstm_max.fit(df=data_train, val_size=365, time_col='time', target_col='temperature_2m_max (°C)', id_col='unique_id')

Seed set to 1


GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
You are using a CUDA device ('NVIDIA GeForce RTX 2050') that has Tensor Cores. To properly utilize them, you should set `torch.set_float32_matmul_precision('medium' | 'high')` which will trade-off precision for performance. For more details, read https://pytorch.org/docs/stable/generated/torch.set_float32_matmul_precision.html#torch.set_float32_matmul_precision
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name         | Type          | Params | Mode 
-------------------------------------------------------
0 | loss         | MSE           | 0      | train
1 | padder_train | ConstantPad1d | 0      | train
2 | scaler       | TemporalNorm  | 0      | train
3 | hist_encoder | LSTM          | 1.3 M  | train
4 | mlp_decoder  | MLP           | 16.6 K | train
-------------------------------------------------------
1.3 M     Trainable params
0         Non-trainable params
1.3 M  

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

`Trainer.fit` stopped: `max_steps=1200` reached.


In [8]:
horizon = 7
model_lstm_min = [LSTM(input_size = 30,            # Length of input sequence
               h=horizon,                    # Forecast horizon
               max_steps = 1200,                # Number of steps to train
               scaler_type='standard',       # Type of scaler to normalize data
               loss=MSE(),            # Loss function to use for training
               learning_rate=0.0001,
               early_stop_patience_steps=10,          # Number of epochs with no improvement after which training will be stopped
               batch_size=128,                  # Size of each batch
               encoder_n_layers=10,             # Number of layers in the encoder LSTM
               encoder_hidden_size=128,       # Defines the size of the hidden state of the LSTM
               decoder_layers=2,             # Number of layers in the decoder LSTM
               decoder_hidden_size=128,)]     # Defines the number of hidden units of each layer of the MLP 
nf_lstm_min = NeuralForecast(models=model_lstm_min, freq='D')
nf_lstm_min.fit(df=data_train, val_size=365, time_col='time', target_col='temperature_2m_min (°C)', id_col='unique_id')

Seed set to 1
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name         | Type          | Params | Mode 
-------------------------------------------------------
0 | loss         | MSE           | 0      | train
1 | padder_train | ConstantPad1d | 0      | train
2 | scaler       | TemporalNorm  | 0      | train
3 | hist_encoder | LSTM          | 1.3 M  | train
4 | mlp_decoder  | MLP           | 16.6 K | train
-------------------------------------------------------
1.3 M     Trainable params
0         Non-trainable params
1.3 M     Total params
5.090     Total estimated model params size (MB)
10        Modules in train mode
0         Modules in eval mode


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

`Trainer.fit` stopped: `max_steps=1200` reached.


In [9]:
"""rolling_forecasts_max_lstm = []
for i in range(1):
    predict_date = data_test.iloc[i]['time']
    record = {'time': predict_date}
    end_i = data.index[data['time'] == predict_date][0]
    input_window = data.iloc[end_i - 30 : end_i]
    print(f"Next 7 Predictions for {predict_date}")
    preds = nf_lstm_max.predict(df=input_window, verbose=False)
    print(preds)
    #record[f'pred_{k}d_before'] = preds.iloc[k-1]['LSTM']
    #rolling_forecasts_max_lstm.append(record)
    
    print(input_window['time'])
rolling_forecasts_max_lstm"""

'rolling_forecasts_max_lstm = []\nfor i in range(1):\n    predict_date = data_test.iloc[i][\'time\']\n    record = {\'time\': predict_date}\n    end_i = data.index[data[\'time\'] == predict_date][0]\n    input_window = data.iloc[end_i - 30 : end_i]\n    print(f"Next 7 Predictions for {predict_date}")\n    preds = nf_lstm_max.predict(df=input_window, verbose=False)\n    print(preds)\n    #record[f\'pred_{k}d_before\'] = preds.iloc[k-1][\'LSTM\']\n    #rolling_forecasts_max_lstm.append(record)\n    \n    print(input_window[\'time\'])\nrolling_forecasts_max_lstm'

## Forecasting with LSTM

In [10]:
rolling_forecasts_max_lstm = []

for i in range(len(data_test)):  # or range(len(data_test))
    predict_date = data_test.iloc[i]['time']
    
    # Find end index for the window ending just before predict_date
    try:
        end_i = data.index[data['time'] == predict_date][0]
    except IndexError:
        print(f"Date {predict_date} not found in `data`, skipping.")
        continue

    input_window = data.iloc[end_i - 30 : end_i]

    preds = nf_lstm_max.predict(df=input_window, verbose=False)

    # Preparing one record with 7 predicted values
    record = {'input_until': predict_date-pd.Timedelta(days=1)}
    for j in range(7):
        record[f'pred_day{j+1}'] = preds.iloc[j]['LSTM']

    rolling_forecasts_max_lstm.append(record)

# Convert to DataFrame
forecast_df_max_lstm = pd.DataFrame(rolling_forecasts_max_lstm)
forecast_df_max_lstm

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.


GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

...

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

input_until  pred_day1  pred_day2  pred_day3  pred_day4  pred_day5  \
0     2020-12-31  24.667791  24.763672  24.817650  24.844782  24.863560   
1     2021-01-01  24.740625  24.784542  24.800611  24.808376  24.816315   
2     2021-01-02  24.785938  24.792635  24.790693  24.789112  24.786942   
3     2021-01-03  24.889257  24.881550  24.875357  24.869076  24.859566   
4     2021-01-04  25.141699  25.133110  25.125849  25.117252  25.107178   
...          ...        ...        ...        ...        ...        ...   
1554  2025-04-03  36.826130  37.076122  37.265038  37.376896  37.391819   
1555  2025-04-04  36.960381  37.131645  37.212257  37.181370  37.025112   
1556  2025-04-05  37.361012  37.454193  37.443790  37.313511  37.075619   
1557  2025-04-06  37.596458  37.582771  37.452602  37.221470  36.928265   
1558  2025-04-07  37.613068  37.469761  37.232479  36.939327  36.635857   

      pred_day6  pred_day7  
0     24.882647  24.900894  
1     24.823484  24.826843  
2     24.781078  24.771812  
3     24.846882  24.832378  
4     25.096180  25.079947  
...         ...        ...  
1554  37.293625  37.068596  
1555  36.759033  36.420597  
1556  36.768936  36.440655  
1557  36.619339  36.327587  
1558  36.358746  36.141266  

[1559 rows x 8 columns]

In [11]:
rolling_forecasts_min_lstm = []

for i in range(len(data_test)):  # or range(len(data_test))
    predict_date = data_test.iloc[i]['time']
    
    # Find end index for the window ending just before predict_date
    try:
        end_i = data.index[data['time'] == predict_date][0]
    except IndexError:
        print(f"Date {predict_date} not found in `data`, skipping.")
        continue

    input_window = data.iloc[end_i - 30 : end_i]

    preds = nf_lstm_min.predict(df=input_window, verbose=False)

    # Preparing one record with 7 predicted values
    record = {'input_until': predict_date-pd.Timedelta(days=1)}
    for j in range(7):
        record[f'pred_day{j+1}'] = preds.iloc[j]['LSTM']

    rolling_forecasts_min_lstm.append(record)

# Convert to DataFrame
forecast_df_min_lstm = pd.DataFrame(rolling_forecasts_min_lstm)
forecast_df_min_lstm

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.


GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

...

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

input_until  pred_day1  pred_day2  pred_day3  pred_day4  pred_day5  \
0     2020-12-31  12.086485  12.154333  12.154835  12.208255  12.369013   
1     2021-01-01  12.054208  12.037779  12.081413  12.240765  12.462977   
2     2021-01-02  11.847878  11.877876  12.035819  12.259152  12.481297   
3     2021-01-03  11.677612  11.832335  12.055666  12.271238  12.421439   
4     2021-01-04  11.762079  11.983528  12.194697  12.333330  12.374684   
...          ...        ...        ...        ...        ...        ...   
1554  2025-04-03  25.389668  25.427753  25.460114  25.477467  25.468483   
1555  2025-04-04  25.627504  25.664631  25.689831  25.694656  25.668901   
1556  2025-04-05  25.822699  25.857424  25.874800  25.867123  25.825924   
1557  2025-04-06  25.902760  25.935873  25.948025  25.933083  25.884872   
1558  2025-04-07  25.966330  25.989971  25.988678  25.957613  25.891201   

      pred_day6  pred_day7  
0     12.591315  12.818899  
1     12.689175  12.866613  
2     12.647032  12.734079  
3     12.481442  12.486939  
4     12.359244  12.354216  
...         ...        ...  
1554  25.418146  25.305712  
1555  25.600248  25.472870  
1556  25.741640  25.601490  
1557  25.795723  25.653625  
1558  25.780741  25.615353  

[1559 rows x 8 columns]

In [35]:
lstm_pred_1 = pd.concat((forecast_df_max_lstm.iloc[:]['pred_day1'], forecast_df_min_lstm.iloc[:]['pred_day1']), axis=1)
lstm_pred_1.columns = ['max', 'min']
lstm_pred_2 = pd.concat((forecast_df_max_lstm.iloc[:-1]['pred_day2'], forecast_df_min_lstm.iloc[:-1]['pred_day2']), axis=1)
lstm_pred_2.columns = ['max', 'min']
lstm_pred_3 = pd.concat((forecast_df_max_lstm.iloc[:-2]['pred_day3'], forecast_df_min_lstm.iloc[:-2]['pred_day3']), axis=1)
lstm_pred_3.columns = ['max', 'min']
lstm_pred_4 = pd.concat((forecast_df_max_lstm.iloc[:-3]['pred_day4'], forecast_df_min_lstm.iloc[:-3]['pred_day4']), axis=1)
lstm_pred_4.columns = ['max', 'min']
lstm_pred_5 = pd.concat((forecast_df_max_lstm.iloc[:-4]['pred_day5'], forecast_df_min_lstm.iloc[:-4]['pred_day5']), axis=1)
lstm_pred_5.columns = ['max', 'min']
lstm_pred_6 = pd.concat((forecast_df_max_lstm.iloc[:-5]['pred_day6'], forecast_df_min_lstm.iloc[:-5]['pred_day6']), axis=1)
lstm_pred_6.columns = ['max', 'min']
lstm_pred_7 = pd.concat((forecast_df_max_lstm.iloc[:-6]['pred_day7'], forecast_df_min_lstm.iloc[:-6]['pred_day7']), axis=1)
lstm_pred_7.columns = ['max', 'min']

In [23]:
forecast_df_max_lstm

input_until  pred_day1  pred_day2  pred_day3  pred_day4  pred_day5  \
0     2020-12-31  24.667791  24.763672  24.817650  24.844782  24.863560   
1     2021-01-01  24.740625  24.784542  24.800611  24.808376  24.816315   
2     2021-01-02  24.785938  24.792635  24.790693  24.789112  24.786942   
3     2021-01-03  24.889257  24.881550  24.875357  24.869076  24.859566   
4     2021-01-04  25.141699  25.133110  25.125849  25.117252  25.107178   
...          ...        ...        ...        ...        ...        ...   
1554  2025-04-03  36.826130  37.076122  37.265038  37.376896  37.391819   
1555  2025-04-04  36.960381  37.131645  37.212257  37.181370  37.025112   
1556  2025-04-05  37.361012  37.454193  37.443790  37.313511  37.075619   
1557  2025-04-06  37.596458  37.582771  37.452602  37.221470  36.928265   
1558  2025-04-07  37.613068  37.469761  37.232479  36.939327  36.635857   

      pred_day6  pred_day7  
0     24.882647  24.900894  
1     24.823484  24.826843  
2     24.781078  24.771812  
3     24.846882  24.832378  
4     25.096180  25.079947  
...         ...        ...  
1554  37.293625  37.068596  
1555  36.759033  36.420597  
1556  36.768936  36.440655  
1557  36.619339  36.327587  
1558  36.358746  36.141266  

[1559 rows x 8 columns]

In [22]:
data_test['time']

16802   2021-01-01
16803   2021-01-02
16804   2021-01-03
16805   2021-01-04
16806   2021-01-05
           ...    
18356   2025-04-04
18357   2025-04-05
18358   2025-04-06
18359   2025-04-07
18360   2025-04-08
Name: time, Length: 1559, dtype: datetime64[ns]

## Evaluation of LSTM results

In [13]:
from sklearn.metrics import root_mean_squared_error, mean_absolute_error, mean_absolute_percentage_error, r2_score

In [39]:
rsme_lstm_1 = root_mean_squared_error(data_test[['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_1)
mae_lstm_1 = mean_absolute_error(data_test[['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_1)
mape_lstm_1 = mean_absolute_percentage_error(data_test[['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_1)
r2_lstm_1 = r2_score(data_test[['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_1)
print(f"For 1 day future -> RMSE: {rsme_lstm_1}, MAE: {mae_lstm_1}, MAPE: {mape_lstm_1}, R2: {r2_lstm_1}")

For 1 day future -> RMSE: 1.8575774281313868, MAE: 1.4047543570351495, MAPE: 0.05777844750215946, R2: 0.8099344884289854


In [ ]:
rsme_lstm_2 = root_mean_squared_error(data_test.iloc[1:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_2)
mae_lstm_2 = mean_absolute_error(data_test.iloc[1:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_2)
mape_lstm_2 = mean_absolute_percentage_error(data_test.iloc[1:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_2)
r2_lstm_2 = r2_score(data_test.iloc[1:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_2)
print(f"For 2 day future -> RMSE: {rsme_lstm_2}, MAE: {mae_lstm_2}, MAPE: {mape_lstm_2}, R2: {r2_lstm_2}")

For 2 day future -> RMSE: 1.9964762083486562, MAE: 1.5133820766355934, MAPE: 0.06223005038111627, R2: 0.7809216177189802


In [43]:
rsme_lstm_3 = root_mean_squared_error(data_test.iloc[2:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_3)
mae_lstm_3 = mean_absolute_error(data_test.iloc[2:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_3)
mape_lstm_3 = mean_absolute_percentage_error(data_test.iloc[2:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_3)
r2_lstm_3 = r2_score(data_test.iloc[2:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_3)
print(f"For 3 day future -> RMSE: {rsme_lstm_3}, MAE: {mae_lstm_3}, MAPE: {mape_lstm_3}, R2: {r2_lstm_3}")

For 3 day future -> RMSE: 2.1022418769109574, MAE: 1.594091967887119, MAPE: 0.06544368934842558, R2: 0.7573936501363742


In [44]:
rsme_lstm_4 = root_mean_squared_error(data_test.iloc[3:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_4)
mae_lstm_4 = mean_absolute_error(data_test.iloc[3:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_4)
mape_lstm_4 = mean_absolute_percentage_error(data_test.iloc[3:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_4)
r2_lstm_4 = r2_score(data_test.iloc[3:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_4)
print(f"For 4 day future -> RMSE: {rsme_lstm_4}, MAE: {mae_lstm_4}, MAPE: {mape_lstm_4}, R2: {r2_lstm_4}")

For 4 day future -> RMSE: 2.1854382250376476, MAE: 1.6546189545972183, MAPE: 0.06779422180985609, R2: 0.7382368865822313


In [49]:
rsme_lstm_5 = root_mean_squared_error(data_test.iloc[4:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_5)
mae_lstm_5 = mean_absolute_error(data_test.iloc[4:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_5)
mape_lstm_5 = mean_absolute_percentage_error(data_test.iloc[4:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_5)
r2_lstm_5 = r2_score(data_test.iloc[4:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_5)
print(f"For 5 day future -> RMSE: {rsme_lstm_5}, MAE: {mae_lstm_5}, MAPE: {mape_lstm_5}, R2: {r2_lstm_5}")

For 5 day future -> RMSE: 2.254665409742862, MAE: 1.7071914833534954, MAPE: 0.06983843084216845, R2: 0.722110260395802


In [50]:
rsme_lstm_6 = root_mean_squared_error(data_test.iloc[5:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_6)
mae_lstm_6 = mean_absolute_error(data_test.iloc[5:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_6)
mape_lstm_6 = mean_absolute_percentage_error(data_test.iloc[5:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_6)
r2_lstm_6 = r2_score(data_test.iloc[5:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_6)
print(f"For 6 day future -> RMSE: {rsme_lstm_6}, MAE: {mae_lstm_6}, MAPE: {mape_lstm_6}, R2: {r2_lstm_6}")

For 6 day future -> RMSE: 2.3208456335030823, MAE: 1.7551784649778979, MAPE: 0.07169637490190714, R2: 0.7066793562052647


In [51]:
rsme_lstm_7 = root_mean_squared_error(data_test.iloc[6:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_7)
mae_lstm_7 = mean_absolute_error(data_test.iloc[6:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_7)
mape_lstm_7 = mean_absolute_percentage_error(data_test.iloc[6:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_7)
r2_lstm_7 = r2_score(data_test.iloc[6:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], lstm_pred_7)
print(f"For 7 day future -> RMSE: {rsme_lstm_7}, MAE: {mae_lstm_7}, MAPE: {mape_lstm_7}, R2: {r2_lstm_7}")

For 7 day future -> RMSE: 2.3929336266493775, MAE: 1.808734543770264, MAPE: 0.07380052391703358, R2: 0.6896457790403201


## Training TimeXer Model

In [7]:
"""horizon = 1
model_lstm = [LSTM(input_size = 30,            # Length of input sequence
               h=horizon,                    # Forecast horizon
               max_steps = 500,                # Number of steps to train
               scaler_type='standard',       # Type of scaler to normalize data
               loss=MSE(),            # Loss function to use for training
               learning_rate=0.0001,
               batch_size=128,                  # Size of each batch
               encoder_n_layers=10,             # Number of layers in the encoder LSTM
               encoder_hidden_size=64,       # Defines the size of the hidden state of the LSTM
               decoder_layers=2,             # Number of layers in the decoder LSTM
               decoder_hidden_size=64,)]     # Defines the number of hidden units of each layer of the MLP 
nf_lstm = NeuralForecast(models=model_lstm, freq='D')
nf_lstm.fit(df=data_train, val_size=len(data_test), time_col='time', target_col='temperature_2m_mean (°C)', id_col='unique_id')"""

"""data_train_timexer = data_train.copy()
data_train_timexer.rename(columns={'time': 'ds'}, inplace=True)
data_train_timexer.rename(columns={'temperature_2m_mean (°C)': 'y'}, inplace=True)"""

model_transformer1 = TimeXer(h=7,
                input_size=30,
                n_series=1,
                batch_size=128,
                patch_len=12,
                hidden_size=128,
                n_heads=16,
                e_layers=2,
                d_ff=256,
                factor=1,
                dropout=0.2,
                use_norm=True,
                loss=MSE(),
                learning_rate=0.0001,
                valid_loss=MAE(),
                early_stop_patience_steps=10,
                max_steps=2000)
nf_transformer_min = NeuralForecast(models=[model_transformer1], freq='D')
nf_transformer_max = NeuralForecast(models=[model_transformer1], freq='D')
nf_transformer_max.fit(df=data_train, val_size=365, time_col='time', target_col='temperature_2m_max (°C)', id_col='unique_id')
nf_transformer_min.fit(df=data_train, val_size=365, time_col='time', target_col='temperature_2m_min (°C)', id_col='unique_id')

Seed set to 1


GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
You are using a CUDA device ('NVIDIA GeForce RTX 2050') that has Tensor Cores. To properly utilize them, you should set `torch.set_float32_matmul_precision('medium' | 'high')` which will trade-off precision for performance. For more details, read https://pytorch.org/docs/stable/generated/torch.set_float32_matmul_precision.html#torch.set_float32_matmul_precision
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name         | Type                   | Params | Mode 
----------------------------------------------------------------
0 | loss         | MSE                    | 0      | train
1 | valid_loss   | MAE                    | 0      | train
2 | padder_train | ConstantPad1d          | 0      | train
3 | scaler       | TemporalNorm           | 0      | train
4 | en_embedding | EnEmbedding            | 1.7 K  | train
5 | ex_embedding | DataEmbedding_inverted | 4.0 K  | train

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

`Trainer.fit` stopped: `max_steps=2000` reached.


In [8]:
nf_transformer_max.save(path='./models/model_max/', model_index=None, overwrite=True, save_dataset=True)
nf_transformer_min.save(path='./models/model_min/', model_index=None, overwrite=True, save_dataset=True)

## Foreacasting with TimeXer

In [9]:
rolling_forecasts_max_timexer = []

for i in range(len(data_test)): 
    predict_date = data_test.iloc[i]['time']
    
    # Find end index for the window ending just before predict_date
    try:
        end_i = data.index[data['time'] == predict_date][0]
    except IndexError:
        print(f"Date {predict_date} not found in `data`, skipping.")
        continue

    input_window = data.iloc[end_i - 30 : end_i]

    preds = nf_transformer_max.predict(df=input_window, verbose=False)

    # Preparing one record with 7 predicted values
    record = {'input_until': predict_date-pd.Timedelta(days=1)}
    for j in range(7):
        record[f'pred_day{j+1}'] = preds.iloc[j]['TimeXer']

    rolling_forecasts_max_timexer.append(record)

# Convert to DataFrame
forecast_df_max_timexer = pd.DataFrame(rolling_forecasts_max_timexer)
forecast_df_max_timexer

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


...

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

input_until  pred_day1  pred_day2  pred_day3  pred_day4  pred_day5  \
0     2020-12-31  25.449728  25.455627  25.399326  25.292961  25.438585   
1     2021-01-01  25.061165  25.162081  25.145922  25.081566  25.237059   
2     2021-01-02  25.106253  25.148937  25.180895  25.077770  25.248415   
3     2021-01-03  25.691990  25.579737  25.527824  25.344231  25.503450   
4     2021-01-04  26.720783  26.396694  26.159231  25.885866  26.015676   
...          ...        ...        ...        ...        ...        ...   
1554  2025-04-03  37.422455  37.236874  37.181282  36.889771  37.270439   
1555  2025-04-04  34.147022  34.516956  35.055073  35.146240  35.676640   
1556  2025-04-05  37.463024  37.214024  37.344131  37.136776  37.438633   
1557  2025-04-06  37.074505  36.875557  37.075474  36.894257  37.206791   
1558  2025-04-07  36.173561  36.125977  36.512398  36.415207  36.793812   

      pred_day6  pred_day7  
0     25.262331  25.212259  
1     25.053137  24.989922  
2     24.994253  24.958584  
3     25.244947  25.244007  
4     25.788059  25.867949  
...         ...        ...  
1554  36.885761  37.112999  
1555  35.537003  35.530392  
1556  36.908321  37.050484  
1557  36.833927  37.024010  
1558  36.537315  36.716171  

[1559 rows x 8 columns]

In [10]:
rolling_forecasts_min_timexer = []

for i in range(len(data_test)):  
    predict_date = data_test.iloc[i]['time']
    
    # Find end index for the window ending just before predict_date
    try:
        end_i = data.index[data['time'] == predict_date][0]
    except IndexError:
        print(f"Date {predict_date} not found in `data`, skipping.")
        continue

    input_window = data.iloc[end_i - 30 : end_i]

    preds = nf_transformer_min.predict(df=input_window, verbose=False)

    # Preparing one record with 7 predicted values
    record = {'input_until': predict_date-pd.Timedelta(days=1)}
    for j in range(7):
        record[f'pred_day{j+1}'] = preds.iloc[j]['TimeXer']

    rolling_forecasts_min_timexer.append(record)

# Convert to DataFrame
forecast_df_min_timexer = pd.DataFrame(rolling_forecasts_min_timexer)
forecast_df_min_timexer

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


...

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

Trainer already configured with model summary callbacks: [<class 'pytorch_lightning.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

input_until  pred_day1  pred_day2  pred_day3  pred_day4  pred_day5  \
0     2020-12-31  13.137679  13.088698  12.985536  13.184299  13.149577   
1     2021-01-01  13.034383  12.943583  12.901439  13.070148  13.003500   
2     2021-01-02  12.500472  12.496919  12.528550  12.693856  12.754368   
3     2021-01-03  12.489101  12.431701  12.506416  12.674364  12.757535   
4     2021-01-04  13.055624  12.854541  12.856647  12.911273  13.059003   
...          ...        ...        ...        ...        ...        ...   
1554  2025-04-03  25.596386  25.663139  25.722109  25.764709  26.236231   
1555  2025-04-04  25.879656  25.907093  26.036579  26.063267  26.594130   
1556  2025-04-05  26.022058  26.056139  26.194601  26.107693  26.681789   
1557  2025-04-06  26.124247  26.149715  26.207762  26.187883  26.662809   
1558  2025-04-07  25.892462  25.931690  26.053654  26.012459  26.498457   

      pred_day6  pred_day7  
0     13.071213  12.807915  
1     12.906763  12.617537  
2     12.607304  12.428665  
3     12.639399  12.500160  
4     12.925626  12.795364  
...         ...        ...  
1554  25.853722  26.044931  
1555  26.133013  26.252419  
1556  26.262943  26.383354  
1557  26.263128  26.371281  
1558  26.163292  26.261915  

[1559 rows x 8 columns]

In [11]:
timexer_pred_1 = pd.concat((forecast_df_max_timexer.iloc[:]['pred_day1'], forecast_df_min_timexer.iloc[:]['pred_day1']), axis=1)
timexer_pred_1.columns = ['max', 'min']
timexer_pred_2 = pd.concat((forecast_df_max_timexer.iloc[:-1]['pred_day2'], forecast_df_min_timexer.iloc[:-1]['pred_day2']), axis=1)
timexer_pred_2.columns = ['max', 'min']
timexer_pred_3 = pd.concat((forecast_df_max_timexer.iloc[:-2]['pred_day3'], forecast_df_min_timexer.iloc[:-2]['pred_day3']), axis=1)
timexer_pred_3.columns = ['max', 'min']
timexer_pred_4 = pd.concat((forecast_df_max_timexer.iloc[:-3]['pred_day4'], forecast_df_min_timexer.iloc[:-3]['pred_day4']), axis=1)
timexer_pred_4.columns = ['max', 'min']
timexer_pred_5 = pd.concat((forecast_df_max_timexer.iloc[:-4]['pred_day5'], forecast_df_min_timexer.iloc[:-4]['pred_day5']), axis=1)
timexer_pred_5.columns = ['max', 'min']
timexer_pred_6 = pd.concat((forecast_df_max_timexer.iloc[:-5]['pred_day6'], forecast_df_min_timexer.iloc[:-5]['pred_day6']), axis=1)
timexer_pred_6.columns = ['max', 'min']
timexer_pred_7 = pd.concat((forecast_df_max_timexer.iloc[:-6]['pred_day7'], forecast_df_min_timexer.iloc[:-6]['pred_day7']), axis=1)
timexer_pred_7.columns = ['max', 'min']

## Evaluation of TimeXer

In [14]:
from sklearn.metrics import root_mean_squared_error, mean_absolute_error, mean_absolute_percentage_error, r2_score

In [15]:
rsme_timexer_1 = root_mean_squared_error(data_test[['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_1)
mae_timexer_1 = mean_absolute_error(data_test[['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_1)
mape_timexer_1 = mean_absolute_percentage_error(data_test[['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_1)
r2_timexer_1 = r2_score(data_test[['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_1)
print(f"For 1 day future -> RMSE: {rsme_timexer_1}, MAE: {mae_timexer_1}, MAPE: {mape_timexer_1}, R2: {r2_timexer_1}")

For 1 day future -> RMSE: 1.3096089628081293, MAE: 0.9873336444534194, MAPE: 0.040737305935170456, R2: 0.9071454048622727


In [16]:
rsme_timexer_2 = root_mean_squared_error(data_test.iloc[1:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_2)
mae_timexer_2 = mean_absolute_error(data_test.iloc[1:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_2)
mape_timexer_2 = mean_absolute_percentage_error(data_test.iloc[1:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_2)
r2_timexer_2 = r2_score(data_test.iloc[1:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_2)
print(f"For 2 day future -> RMSE: {rsme_timexer_2}, MAE: {mae_timexer_2}, MAPE: {mape_timexer_2}, R2: {r2_timexer_2}")

For 2 day future -> RMSE: 1.6998872988244869, MAE: 1.2923696975805945, MAPE: 0.05378680207161202, R2: 0.8436666424407724


In [17]:
rsme_timexer_3 = root_mean_squared_error(data_test.iloc[2:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_3)
mae_timexer_3 = mean_absolute_error(data_test.iloc[2:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_3)
mape_timexer_3 = mean_absolute_percentage_error(data_test.iloc[2:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_3)
r2_timexer_3 = r2_score(data_test.iloc[2:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_3)
print(f"For 3 day future -> RMSE: {rsme_timexer_3}, MAE: {mae_timexer_3}, MAPE: {mape_timexer_3}, R2: {r2_timexer_3}")

For 3 day future -> RMSE: 1.9298102487930722, MAE: 1.4700747576905278, MAPE: 0.06132653564103423, R2: 0.797709167219709


In [18]:
rsme_timexer_4 = root_mean_squared_error(data_test.iloc[3:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_4)
mae_timexer_4 = mean_absolute_error(data_test.iloc[3:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_4)
mape_timexer_4 = mean_absolute_percentage_error(data_test.iloc[3:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_4)
r2_timexer_4 = r2_score(data_test.iloc[3:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_4)
print(f"For 4 day future -> RMSE: {rsme_timexer_4}, MAE: {mae_timexer_4}, MAPE: {mape_timexer_4}, R2: {r2_timexer_4}")

For 4 day future -> RMSE: 2.087829022173322, MAE: 1.5927640319176994, MAPE: 0.06620172349305284, R2: 0.7627168847173842


In [21]:
rsme_timexer_5 = root_mean_squared_error(data_test.iloc[4:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_5)
mae_timexer_5 = mean_absolute_error(data_test.iloc[4:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_5)
mape_timexer_5 = mean_absolute_percentage_error(data_test.iloc[4:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_5)
r2_timexer_5 = r2_score(data_test.iloc[4:][['temperature_2m_max (°C)', 'temperature_2m_min (°C)']], timexer_pred_5)
print(f"For 5 day future -> RMSE: {rsme_timexer_5}, MAE: {mae_timexer_5}, MAPE: {mape_timexer_5}, R2: {r2_timexer_5}")

For 5 day future -> RMSE: 2.177988007969941, MAE: 1.667702322220879, MAPE: 0.06959593062215744, R2: 0.7413860207959644


In [ ]:
root_mean_squared_error(data_test['temperature_2m_max (°C)'], timexer_pred_1)

In [ ]:
rolling_forecasts_transformer1 = []

for i in range(len(data_test)):
    # Get the current date we want to predict
    predict_date = data_test.iloc[i]['time']

    # Grab last 30 days of data ending at day before prediction
    end_index = data[data['time'] == predict_date].index[0]
    input_window = data.iloc[end_index - 30:end_index]


    pred = nf_transformer1.predict(df=input_window, verbose=True)

    rolling_forecasts_transformer1.append({
        'time': predict_date,
        'TimeXer': pred.iloc[0]['TimeXer']
    })

In [ ]:
rolling_forecasts_transformer1_data = pd.DataFrame(rolling_forecasts_transformer1)
rolling_forecasts_transformer1_data.head(10)

In [92]:
timexer_rsme = root_mean_squared_error(data_test['temperature_2m_mean (°C)'], rolling_forecasts_transformer1_data['TimeXer'])
timexer_mae = mean_absolute_error(data_test['temperature_2m_mean (°C)'], rolling_forecasts_transformer1_data['TimeXer'])
timexer_mape = mean_absolute_percentage_error(data_test['temperature_2m_mean (°C)'], rolling_forecasts_transformer1_data['TimeXer'])
timexer_r2 = r2_score(data_test['temperature_2m_mean (°C)'], rolling_forecasts_transformer1_data['TimeXer'])
print(f"RSME: {timexer_rsme}, MAE: {timexer_mae}, MAPE: {timexer_mape}, R2: {timexer_r2}")

RSME: 1.1016326645804828, MAE: 0.8611505781250784, MAPE: 0.034977939979408415, R2: 0.9294253601440261


## Training TimesNet Model